# Collatz Sequence

Starting with any positive integer:
* if n is even, the next number in the sequence is n / 2
* if n is odd, the next number in the sequence is 3n + 1

$$
Collatz(N) = 
\begin{cases}
  N / 2 & \text{if } N \% 2 = 0 \\
  3N + 1 & \text{if } N \% 2 \ne 0
\end{cases}
, N \in \mathbb{Z}^{+}
$$

It is conjectured that every such sequence eventually reaches the number 1. 

Test this conjecture.

Bonus: What input n <= 1000000 gives the longest sequence?

## Initial Thoughts 

Before diving into the problem, let's think about this problem analytically. In order for the sequence to converge to 1, we must reach some odd number that, when mapped by the Collatz sequence, becomes a power of 2. So how likely do we think that is to occur for any given odd number?

Let's take a sample of odd numbers and see what happens when we map them using Collatz.

| N | 3*N + 1 | Is a power of 2? |
| ---- | ---- | ---- |
| 5 | 16 | Yes |
| 11 | 34 | No |
| 25 | 76 | No |
| 37 | 112 | No |
| 159 | 478 | No |
| 75289 | 225868 | No |

From a semi-random sample, it doesn't seem all that common to occur. But, that's alright because the sequence can continue from there.

We could actually look at this situation graphically!

In [5]:
!pip install --user plotly
!pip install --user nbformat


   ---------------------------------------- 0/6 [fastjsonschema]
   ------ --------------------------------- 1/6 [rpds-py]
   ------------- -------------------------- 2/6 [referencing]
   -------------------- ------------------- 3/6 [jsonschema-specifications]
   -------------------- ------------------- 3/6 [jsonschema-specifications]
   -------------------------- ------------- 4/6 [jsonschema]
   -------------------------- ------------- 4/6 [jsonschema]
   -------------------------- ------------- 4/6 [jsonschema]
   -------------------------- ------------- 4/6 [jsonschema]
   --------------------------------- ------ 5/6 [nbformat]
   --------------------------------- ------ 5/6 [nbformat]
   --------------------------------- ------ 5/6 [nbformat]
   --------------------------------- ------ 5/6 [nbformat]
   --------------------------------- ------ 5/6 [nbformat]
   --------------------------------- ------ 5/6 [nbformat]
   --------------------------------- ------ 5/6 [nbformat]
   --

In [1]:
import plotly.graph_objects as go

def nearest_power_of_2_int(p): # bit-wise math!! :)
    lower = 1 << (p.bit_length() - 1)
    upper = lower << 1
    return lower if p - lower < upper - p else upper

X = [i for i in range(1, 50)]
oddN = [2 * i - 1 for i in X]
collatzOddMap = [3*i + 1 for i in oddN]
nearestPowerOfTwoToCollatzOdd = [nearest_power_of_2_int(i) for i in collatzOddMap]

fig = go.Figure()
fig.add_trace(go.Scatter(x=oddN, y=collatzOddMap, mode='lines+markers', name='Collatz Odd Mapping'))
fig.add_trace(go.Scatter(x=oddN, y=nearestPowerOfTwoToCollatzOdd, mode='lines+markers', name='Nearest Power of 2'))
fig.update_layout(title='Comparing the Collatz Sequence (Odd Number Map) to Powers of 2', xaxis_title='Odd Numbers', yaxis_title='Collatz Mapping for Odd Numbers')
fig.show()

As you may observe, the likelihood for any given odd number converging to a power of 2 decreases as that odd number increases. 

Now I'm left wondering, just how large of numbers get included in this sequence?

## Evaluate the Magnitude of Odd Numbers contained in the Collatz Sequence

One way to think about this is: how would we expect to see the Collatz Sequence continue to grow in magnitude? Simply put, as long as the mapping function $3N - 1$ continues to yield odd numbers OR even numbers that are distant from powers of 2. 

But how bad is it to be distant from powers of 2? As a note for the future, it may be interesting to explore this. TODO

In [2]:
def next_collatz(N, sequence):
    sequence.append(N)
    if N < 1:
        return None
    if N == 1:
        # print(f'N={N}, sequence has converged, sequence length is: {len(sequence)}')
        return sequence
    elif N % 2 == 0:
        # print(f'N={N} is even, current sequence length is: {len(sequence)}')
        next_collatz(N/2, sequence)
    else:
        # print(f'N={N} is odd, current sequence length is: {len(sequence)}')
        next_collatz(3*N + 1, sequence)
    return sequence

In [3]:
fig = go.Figure()
for i in range(1, 10):
    i_sequence = next_collatz(i, [])
    X = [i for i in range(len(i_sequence))]
    fig.add_trace(go.Scatter(x=X, y=i_sequence, mode='lines+markers', name=f'N={i}'))

fig.update_layout(title='Collatz Sequences (N < 10)', xaxis_title='Sequence Ordinal', yaxis_title='Collatz Magnitude')
fig.show()

Interestingly, based on $N<10$, we can see that:
* Powers of 2 represent LOCAL $max(Magnitude)$ (prior to convergence, importantly), but not necessarily the GLOBAL $max(Magnitude)$ for a given $N$
* GLOBAL $max(Magnitude)$ repeats between sequences 
  * the presence of a repeated GLOBAL $max(Magnitude)$ _may_ signal upcoming convergence (we should test this with larger $N$)

Now let's look at larger numbers of $N$.

In [4]:
# skip powers of 2, since those are boring
def is_power_of_2(p):
    return p > 0 and (p & (p - 1)) == 0 # powers of 2 only have one bit set

fig = go.Figure()
for i in [x for x in range(10, 100) if not is_power_of_2(x)]:
    i_sequence = next_collatz(i, [])
    X = [i for i in range(len(i_sequence))]
    fig.add_trace(go.Scatter(x=X, y=i_sequence, mode='lines+markers', name=f'N={i}'))

fig.update_layout(title='Collatz Sequences (10 < N < 100), Ignoring Powers of 2', xaxis_title='Sequence Ordinal', yaxis_title='Collatz Magnitude')
fig.show()

It seeems to me that we could save some compute time by instituting a stopping condition if we hit a GLOBAL $max(Magnitude)$. We could certainly skip any $N = \text{previous GLOBAL } max(Magnitude)$

## Optimizations!

In [5]:
import numpy as np
import pandas as pd

collatz_df = pd.DataFrame({
    'N' : pd.Series(dtype='int'),       # starting N
    'MAX_MAG': pd.Series(dtype='int'),  # Maximum Magnitude of Collatz Sequence beginning with N
    'SEQ_LEN': pd.Series(dtype='int')   # Sequence Length of Collatz Sequence beginning with N
})

fig = go.Figure()
for i in range(1, 20):
    if i in collatz_df['N']:
        continue # already in the dataframe (and thus, not novel)
    i_sequence = next_collatz(i, [])
    
    X = [i for i in range(len(i_sequence))]
    fig.add_trace(go.Scatter(x=X, y=i_sequence, mode='lines+markers', name=f'N={i}'))


    maxMag = max(i_sequence)
    seqLen = len(i_sequence)
    # determine the remaining length after the maxMag
    seqLenAfterMaxMag = seqLen - i_sequence.index(maxMag)

    collatz_df.loc[i] = {'N': i, 'MAX_MAG': maxMag, 'SEQ_LEN': seqLen}
    collatz_df.loc[maxMag] = {'N': maxMag, 'MAX_MAG': maxMag, 'SEQ_LEN': seqLenAfterMaxMag}

fig.update_layout(title='Collatz Sequences (N < 20), Slight Optimization', xaxis_title='Sequence Ordinal', yaxis_title='Collatz Magnitude')
fig.show()

print(collatz_df.head(20))

           N  MAX_MAG  SEQ_LEN
1.0      1.0      1.0        1
2.0      2.0      2.0        2
3.0      3.0     16.0        8
16.0    16.0     16.0        5
4.0      4.0      4.0        3
5.0      5.0     16.0        6
6.0      6.0     16.0        9
7.0      7.0     52.0       17
52.0    52.0     52.0       12
8.0      8.0      8.0        4
9.0      9.0     52.0       20
10.0    10.0     16.0        7
11.0    11.0     52.0       15
12.0    12.0     16.0       10
13.0    13.0     40.0       10
40.0    40.0     40.0        9
14.0    14.0     52.0       18
15.0    15.0    160.0       18
160.0  160.0    160.0       11
17.0    17.0     52.0       13


That's neat, but not complete! As you can see from the `MAX_MAG` column, there are repetitions that we aren't optimizing for. Specifically, *16* and *52* have repeated a number of times and each would offer a decent reduction in looping.

One observation I'll make now that we should clean up in the future (**TODO**): We should take into account any local-maxima that occur after the global maximum. For example, after 52 is found as a global maximum for $N=7$, 40 is seen as a local maxima on the way to 16 (another local maxima). 16 was discovered already as a global maximum of $N=3$, but 40 isn't found as a global maximum until $N=13$. I expect this will be a pattern and could be optimized.

Let's revisit the `next_collatz` function.

In [6]:
collatz_df_opt = pd.DataFrame({
    'N' : pd.Series(dtype='int'),       # starting N
    'MAX_MAG': pd.Series(dtype='int'),  # (global) Maximum Magnitude of Collatz Sequence beginning with N
    'SEQ_LEN': pd.Series(dtype='int'),  # Sequence Length of Collatz Sequence beginning with N
    'REMAIN': pd.Series(dtype='object') # Remainder of sequence after the Global Maximum (helpful for optimization)
})

def next_collatz_optimized(N, sequence):
    '''Recursive function to generate the Collatz Sequence, given a starting positive integer `N`'''
    if N in collatz_df_opt['N']:
        sequence += collatz_df_opt.loc[N]['REMAIN']
        return sequence
    sequence.append(N)
    if N < 1:
        return None
    if N == 1:
        return sequence
    elif N % 2 == 0:
        next_collatz_optimized(N/2, sequence)
    else:
        next_collatz_optimized(3*N + 1, sequence)
    return sequence

def determine_collatz_sequences(upper):
    '''Map the Collatz Sequences up to some specified `upper` value of `N`.
        Along the way, collect significant metrics about the sequences and
        plot the novel sequences via plotly'''
    fig = go.Figure()
    for i in range(1, upper):
        if i in collatz_df_opt['N']:
            continue # already in the dataframe (and thus, not novel)
        i_sequence = next_collatz_optimized(i, [])
        
        maxMag = max(i_sequence)
        seqLen = len(i_sequence)
        seqLenAfterMaxMag = seqLen - i_sequence.index(maxMag)
        remainder = i_sequence[i_sequence.index(maxMag):]

        X = [i for i in range(len(i_sequence))]
        fig.add_trace(go.Scatter(x=X, y=i_sequence, mode='lines+markers', name=f'N={i}'))

        collatz_df_opt.loc[i] = {'N': i, 'MAX_MAG': maxMag, 'SEQ_LEN': seqLen, 'REMAIN': remainder}
        collatz_df_opt.loc[maxMag] = {'N': maxMag, 'MAX_MAG': maxMag, 'SEQ_LEN': seqLenAfterMaxMag, 'REMAIN': remainder}

    fig.update_layout(title=f'Collatz Sequences (N < {upper}), More Optimization', xaxis_title='Sequence Ordinal', yaxis_title='Collatz Magnitude')
    fig.show()

    return collatz_df_opt

In [7]:
collatz_sequences = determine_collatz_sequences(100)
collatz_sequences

N  MAX_MAG  SEQ_LEN  \
1.0      1.0      1.0        1   
2.0      2.0      2.0        2   
3.0      3.0     16.0        8   
16.0    16.0     16.0        5   
4.0      4.0      4.0        3   
...      ...      ...      ...   
96.0    96.0     96.0        8   
97.0    97.0   9232.0       31   
98.0    98.0    148.0       16   
99.0    99.0    448.0       18   
448.0  448.0    448.0       15   

                                                  REMAIN  
1.0                                                  [1]  
2.0                                               [2, 1]  
3.0                               [16.0, 8.0, 4.0, 2, 1]  
16.0                              [16.0, 8.0, 4.0, 2, 1]  
4.0                                            [4, 2, 1]  
...                                                  ...  
96.0                  [96, 48, 24, 16.0, 8.0, 4.0, 2, 1]  
97.0   [9232.0, 4616.0, 2308.0, 1154.0, 577.0, 1732.0...  
98.0   [148, 74.0, 112, 56.0, 52.0, 26.0, 13.0, 40.0,...  
99.0   [448.0, 224.0, 112, 56.0, 52.0, 26.0, 13.0, 40...  
448.0  [448.0, 224.0, 112, 56.0, 52.0, 26.0, 13.0, 40...  

[117 rows x 4 columns]

In [10]:
collatz_sequences.sort_values(by='N', inplace=True)

fig = go.Figure()
fig.add_trace(go.Scatter(x=collatz_sequences['N'], y=collatz_sequences['MAX_MAG'], mode='lines+markers', name='Global Maximum Magnitude'))
fig.add_trace(go.Scatter(x=collatz_sequences['N'], y=collatz_sequences['SEQ_LEN'], mode='lines+markers', name='Sequence Length'))
fig.update_layout(title='Metrics from Collatz Sequences', xaxis_title='N', yaxis_title='Metric value')
fig.show()

In [12]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=collatz_sequences['SEQ_LEN'], y=collatz_sequences['MAX_MAG'], mode='markers', name='Correlation?'))
fig.update_layout(title='Correlation between Sequence Length and Global Maximum Magnitude', xaxis_title='Sequence Length', yaxis_title='Global Maximum Magnitude')
fig.show()

It seems like there's a loose correlation, but we may be missing some data. My optimizations may have limited the number of data points we're seeing. Or perhaps my upper limit on $N$ is conveniently (or not) at the cusp of some leap in behavior.

# Bonus

Let's figure out how long is the longest sequence where starting N <= 1,000,000

In [ ]:
max_seq_len = 1
for i in range(1,1000000):
    i_sequence = next_collatz(i, [])
    # print(f'When N={i}, Sequence Length is: {len(i_sequence)}')
    if len(i_sequence) > max_seq_len:
        max_seq_len = len(i_sequence)

print(f'Max Sequence Length Where N <= 1000000 is: {max_seq_len}')

When N=1, Sequence Length is: 1
When N=2, Sequence Length is: 2
When N=3, Sequence Length is: 8
When N=4, Sequence Length is: 3
When N=5, Sequence Length is: 6
When N=6, Sequence Length is: 9
When N=7, Sequence Length is: 17
When N=8, Sequence Length is: 4
When N=9, Sequence Length is: 20
When N=10, Sequence Length is: 7
When N=11, Sequence Length is: 15
When N=12, Sequence Length is: 10
When N=13, Sequence Length is: 10
When N=14, Sequence Length is: 18
When N=15, Sequence Length is: 18
When N=16, Sequence Length is: 5
When N=17, Sequence Length is: 13
When N=18, Sequence Length is: 21
When N=19, Sequence Length is: 21
When N=20, Sequence Length is: 8
When N=21, Sequence Length is: 8
When N=22, Sequence Length is: 16
When N=23, Sequence Length is: 16
When N=24, Sequence Length is: 11
When N=25, Sequence Length is: 24
When N=26, Sequence Length is: 11
When N=27, Sequence Length is: 112
When N=28, Sequence Length is: 19
When N=29, Sequence Length is: 19
When N=30, Sequence Length is: 19

KeyboardInterrupt: 

This was taking a long time to run in Jupyter. So I separated it out to `collatz.py` and ran that in the background. After some time, it determined that: Max Sequence Length Where N <= 1000000 is: 525.

I want to check this result, but it'll suffice for initial/immediate submission.